<a href="https://colab.research.google.com/github/praneshnikhar/Deep-Learning-models/blob/main/fake_news_classifier_using_LSTM.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import pandas as pd


In [ ]:
df = pd.read_csv('/content/True.csv')

In [ ]:
df.head()

title  \
0  As U.S. budget fight looms, Republicans flip t...   
1  U.S. military to accept transgender recruits o...   
2  Senior U.S. Republican senator: 'Let Mr. Muell...   
3  FBI Russia probe helped by Australian diplomat...   
4  Trump wants Postal Service to charge 'much mor...   

                                                text       subject  \
0  WASHINGTON (Reuters) - The head of a conservat...  politicsNews   
1  WASHINGTON (Reuters) - Transgender people will...  politicsNews   
2  WASHINGTON (Reuters) - The special counsel inv...  politicsNews   
3  WASHINGTON (Reuters) - Trump campaign adviser ...  politicsNews   
4  SEATTLE/WASHINGTON (Reuters) - President Donal...  politicsNews   

                 date  
0  December 31, 2017   
1  December 29, 2017   
2  December 31, 2017   
3  December 30, 2017   
4  December 29, 2017

In [ ]:
df = df.dropna()

In [ ]:
X = df.drop('date',axis=1)
y = df['date']

In [ ]:
X.shape

(21417, 3)

In [ ]:
y.shape

(21417,)

In [ ]:
import tensorflow as tf

In [ ]:
from tensorflow.keras.layers import Embedding
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import Sequential
from tensorflow.keras.preprocessing.text import one_hot
from tensorflow.keras.layers import LSTM
from tensorflow.keras.layers import Dense

In [ ]:
voc_size = 5000

In [ ]:
messages = X.copy()

In [ ]:
messages.reset_index(inplace = True)

In [ ]:
import nltk
import re
from nltk.corpus import stopwords

In [ ]:

from nltk.stem.porter import PorterStemmer
ps = PorterStemmer()
corpus = []
for i in range(0,len(messages)):
  review = re.sub('[^a-zA-Z]',' ',messages['text'][i])
  review = review.lower()
  review = review.split()

  review = [ps.stem(word)for word in review if not word in stopwords.words('english')]
  review = ' '.join(review)
  corpus.append(review)

In [ ]:
corpus

['washington reuter head conserv republican faction u congress vote month huge expans nation debt pay tax cut call fiscal conserv sunday urg budget restraint keep sharp pivot way among republican u repres mark meadow speak cb face nation drew hard line feder spend lawmak brace battl januari return holiday wednesday lawmak begin tri pass feder budget fight like link issu immigr polici even novemb congression elect campaign approach republican seek keep control congress presid donald trump republican want big budget increas militari spend democrat also want proport increas non defens discretionari spend program support educ scientif research infrastructur public health environment protect trump administr alreadi will say go increas non defens discretionari spend percent meadow chairman small influenti hous freedom caucu said program democrat say enough need give govern pay rais percent fiscal conserv see rational eventu run peopl money said meadow among republican vote late decemb parti 

In [30]:
onehot_repr = [one_hot(words,voc_size)for words in corpus]
onehot_repr

[[4039,
  2408,
  913,
  2827,
  4259,
  2183,
  4594,
  2003,
  3384,
  4691,
  1959,
  3299,
  528,
  140,
  1499,
  1295,
  2942,
  103,
  1009,
  2827,
  10,
  3694,
  2403,
  4561,
  4458,
  1370,
  3561,
  4718,
  2576,
  4259,
  4594,
  4066,
  3141,
  2771,
  1569,
  256,
  758,
  528,
  2567,
  4372,
  4869,
  1404,
  4321,
  1186,
  3387,
  546,
  2165,
  3579,
  4538,
  1051,
  1186,
  4894,
  2105,
  1560,
  1404,
  2403,
  470,
  2285,
  151,
  279,
  4507,
  2372,
  2904,
  2194,
  2333,
  3591,
  4730,
  818,
  4259,
  3502,
  4458,
  4421,
  2003,
  1042,
  2855,
  4680,
  4259,
  3434,
  2640,
  2403,
  4287,
  4636,
  4321,
  3065,
  1978,
  3434,
  4987,
  4287,
  1254,
  2040,
  3986,
  4321,
  2302,
  74,
  2580,
  4764,
  975,
  1451,
  364,
  1960,
  2111,
  978,
  4680,
  4719,
  183,
  4818,
  1568,
  1222,
  4287,
  1254,
  2040,
  3986,
  4321,
  828,
  2771,
  4115,
  3950,
  2691,
  991,
  2052,
  2945,
  2095,
  2302,
  3065,
  1568,
  3150,
  681,
  1074,

In [31]:
sent_length = 20
embedded_docs = pad_sequences(onehot_repr,padding='pre',maxlen = sent_length)
print(embedded_docs)

[[1260  527 4106 ... 3315 3384 1260]
 [2964 1629  606 ... 1964 1261 1393]
 [4493 4718 4251 ... 1777 4430 2095]
 ...
 [2165 4090 1404 ...  554 4978 4149]
 [4440  739  379 ...  379 3293 2944]
 [3431 4876 1042 ... 4817  846  342]]


In [33]:
len(embedded_docs)

2887

In [35]:
embedding_vector_features = 40
model= Sequential()
model.add(Embedding(voc_size,embedding_vector_features,input_length=sent_length))
model.add(LSTM(100))
model.add(Dense(1,activation='sigmoid'))
model.compile(loss='binary_crossentropy',optimizer='adam',metrics=['accuracy'])
print(model.summary())

/usr/local/lib/python3.11/dist-packages/keras/src/layers/core/embedding.py:90: UserWarning: Argument `input_length` is deprecated. Just remove it.
  warnings.warn(


Model: "sequential_1"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ embedding (Embedding)           │ ?                      │   0 (unbuilt) │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ lstm (LSTM)                     │ ?                      │   0 (unbuilt) │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense (Dense)                   │ ?                      │   0 (unbuilt) │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 0 (0.00 B)

 Trainable params: 0 (0.00 B)

 Non-trainable params: 0 (0.00 B)

None


In [36]:
import numpy as np
X_final = np.array(embedded_docs)
y_final = np.array(y)

In [37]:
X_final.shape,y_final.shape

((2887, 20), (21417,))

In [40]:

y_final = y_final[:len(X_final)]
X_final = X_final[:len(y_final)]

from sklearn.model_selection import train_test_split
X_train,X_test,y_train,y_test = train_test_split(X_final,y_final,test_size=0.33,random_state=42)